In [4]:
import pandas as pd
import matplotlib.pyplot as plt
%matplotlib inline
plt.style.use('seaborn')
import seaborn as sns
import numpy as np
from scipy.stats import norm, skew
from sklearn.metrics import mean_squared_error

In [220]:
x_train = pd.read_csv('train_mod.csv')
x_test = pd.read_csv('test_mod.csv')
y_train = pd.read_csv('y_train.csv')
df_test = pd.read_csv('test.csv')

In [267]:
from sklearn.linear_model import Ridge, Lasso, ElasticNet, RidgeCV, LassoCV, ElasticNetCV
from sklearn.ensemble import GradientBoostingRegressor 
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import RobustScaler
from sklearn.model_selection import KFold, cross_val_score, train_test_split, GridSearchCV
from sklearn.metrics import mean_squared_error
from mlxtend.regressor import StackingRegressor
import xgboost as xgb
from sklearn.svm import SVR

Train-Test split

In [280]:
tsx_train, tsx_test, tsy_train, tsy_test = train_test_split(x_train, y_train, test_size=0.3, random_state=0)

### Ridge

In [28]:
ridge = Ridge()
para_ridge = {"alpha": np.logspace(0.8,1.1,100)}
gs_ridge = GridSearchCV(ridge, para_ridge, cv=10, scoring='neg_mean_squared_error', n_jobs=-1)
gs_ridge.fit(x_train, y_train)
gs_ridge.best_params_
#{'alpha': 9.930467558623954}

/usr/local/lib/python3.7/site-packages/sklearn/linear_model/ridge.py:147: LinAlgWarning: Ill-conditioned matrix (rcond=1.32007e-249): result may not be accurate.
  overwrite_a=True).T


{'alpha': 9.930467558623954}

In [235]:
ridge = make_pipeline(RobustScaler(), Ridge(alpha = gs_ridge.best_params_['alpha'], random_state=1))
ridge.fit(x_train, y_train)
score_ridge = ridge.score(x_train, y_train)
rmse_ridge = np.sqrt(mean_squared_error(y_train,ridge.predict(x_train)))
ridge_pred = np.expm1(ridge.predict(x_test))

In [293]:
rmse_ridge_train = np.sqrt(mean_squared_error(tsy_train,ridge.predict(tsx_train)))
rmse_ridge_test = np.sqrt(mean_squared_error(tsy_test,ridge.predict(tsx_test)))

In [294]:
print(rmse_ridge_train)
print(rmse_ridge_test)
print(rmse_ridge_test-rmse_ridge_train)

0.09763336846011357
0.0972179374193285
-0.00041543104078506365


Ridge train test split

In [291]:
ridgecv = RidgeCV(alphas=np.logspace(-4,3,1000), normalize=False, cv=10)
ridgecv.fit(tsx_train,tsy_train)

rdg_trainRMSE = np.sqrt(mean_squared_error(tsy_train, ridgecv.predict(tsx_train)))
rdg_testRMSE = np.sqrt(mean_squared_error(tsy_test, ridgecv.predict(tsx_test)))

In [292]:
print(ridgecv.score(tsx_train,tsy_train))
print(ridgecv.score(tsx_test,tsy_test))
print(rdg_trainRMSE)
print(rdg_testRMSE)
print(rdg_testRMSE-rdg_trainRMSE)

0.9388474627384564
0.9293056850604047
0.09755477760450214
0.10931960404080852
0.011764826436306386


### Lasso

In [19]:
lasso = Lasso()
para_lasso = {"alpha": np.logspace(-4,-3.3,100)}
lasso.set_params(max_iter = 10000)
gs_lasso = GridSearchCV(lasso, para_lasso, cv=10, scoring='neg_mean_squared_error', n_jobs=-1)
gs_lasso.fit(x_train, y_train)
gs_lasso.best_params_
#{'alpha': 0.0003503034741265338}

{'alpha': 0.0003503034741265338}

In [232]:
lasso = make_pipeline(RobustScaler(), Lasso(alpha =gs_lasso.best_params_['alpha'], random_state=1))
lasso.fit(x_train, y_train)
score_lasso = lasso.score(x_train, y_train)
rmse_lasso = np.sqrt(mean_squared_error(y_train,lasso.predict(x_train)))
lasso_pred = np.expm1(lasso.predict(x_test))

Lasso train test split

In [285]:
lassocv = LassoCV(alphas=np.logspace(-4,3,10000), normalize=False, max_iter=10000, n_jobs=-1, cv=10)

lassocv.fit(tsx_train,tsy_train)

lso_trainRMSE = np.sqrt(mean_squared_error(tsy_train, lassocv.predict(tsx_train)))
lso_testRMSE = np.sqrt(mean_squared_error(tsy_test, lassocv.predict(tsx_test)))

/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:1100: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


In [284]:
# With normalization
print(lassocv.score(tsx_train,tsy_train))
print(lassocv.score(tsx_test,tsy_test))
print(trainRMSE)
print(testRMSE)
print(testRMSE-trainRMSE)

0.9378252494284984
0.9301590526357314
0.09836675132898118
0.10865778952000578
0.010291038191024601


In [312]:
# Without normalization
print(lassocv.score(tsx_train,tsy_train))
print(lassocv.score(tsx_test,tsy_test))
print(lso_trainRMSE)
print(lso_testRMSE)
print(lso_testRMSE-lso_trainRMSE)

0.9371802759532423
0.9311041444588769
0.09887564165744822
0.10792010360592724
0.009044461948479021


### ElasticNet

In [47]:
ElNet = ElasticNet()
para_ElNet = {"alpha": np.logspace(-3.8,-3.3,10),"l1_ratio": np.linspace(0.7,0.9,10)}
ElNet.set_params(max_iter = 5000)
gs_ElNet = GridSearchCV(ElNet, para_ElNet, cv=10, scoring='neg_mean_squared_error', n_jobs=-1)
gs_ElNet.fit(x_train, y_train)
gs_ElNet.best_params_
#{'alpha': 0.0003880510732210184, 'l1_ratio': 0.9}

/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:475: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 8.110620226919156, tolerance: 0.023278539201380233
  positive)


{'alpha': 0.0003880510732210184, 'l1_ratio': 0.9}

In [229]:
ElNet.set_params(alpha = gs_ElNet.best_params_['alpha'],l1_ratio=gs_ElNet.best_params_['l1_ratio'])
ElNet.fit(x_train, y_train)
score_ElNet = ElNet.score(x_train, y_train)
rmse_ElNet = np.sqrt(mean_squared_error(y_train,ElNet.predict(x_train)))
ElNet_pred = np.expm1(ElNet.predict(x_test))

ElasticNet train test split

In [295]:
enetcv = ElasticNetCV(l1_ratio=np.linspace(0,1,100), alphas=np.logspace(-4,3,1000), max_iter=1000, normalize=False, cv=10, n_jobs=-1)
enetcv.fit(tsx_train,tsy_train)

net_trainRMSE = np.sqrt(mean_squared_error(tsy_train, enetcv.predict(tsx_train)))
net_testRMSE = np.sqrt(mean_squared_error(tsy_test, enetcv.predict(tsx_test)))

/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:1100: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: UserWarning: Coordinate descent with alpha=0 may lead to unexpected results and is discouraged.
  tol, rng, random, positive)
/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: UserWarning: Coordinate descent with alpha=0 may lead to unexpected results and is discouraged.
  tol, rng, random, positive)
/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 28.966434238422135, tolerance: 0.014508286297718963
  tol, rng, random, positive)
/usr/local/lib

/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 28.672079097700827, tolerance: 0.014508286297718963
  tol, rng, random, positive)
/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: UserWarning: Coordinate descent with alpha=0 may lead to unexpected results and is discouraged.
  tol, rng, random, positive)
/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 27.783304358853055, tolerance: 0.013965771965650428
  tol, rng, random, positive)
/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: UserWarning: Coordinate descent with alpha=0 may lead to unexpected results and is discouraged.
  tol, rng, random, positive)
/usr/loc

/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: UserWarning: Coordinate descent with alpha=0 may lead to unexpected results and is discouraged.
  tol, rng, random, positive)
/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 27.668912455688666, tolerance: 0.014558481930201072
  tol, rng, random, positive)
/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: UserWarning: Coordinate descent with alpha=0 may lead to unexpected results and is discouraged.
  tol, rng, random, positive)
/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 27.498550989558474, tolerance: 0.013965771965650428
  tol, rng, random, positive)
/usr/loc

/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 28.07903176040583, tolerance: 0.014508286297718963
  tol, rng, random, positive)
/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: UserWarning: Coordinate descent with alpha=0 may lead to unexpected results and is discouraged.
  tol, rng, random, positive)
/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 27.1467436843237, tolerance: 0.013552634226634962
  tol, rng, random, positive)
/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: UserWarning: Coordinate descent with alpha=0 may lead to unexpected results and is discouraged.
  tol, rng, random, positive)
/usr/local/

/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 26.99476722116204, tolerance: 0.013965771965650428
  tol, rng, random, positive)
/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 27.855423625819128, tolerance: 0.014508286297718963
  tol, rng, random, positive)
/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: UserWarning: Coordinate descent with alpha=0 may lead to unexpected results and is discouraged.
  tol, rng, random, positive)
/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 26.928045310994918, t

...

/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 1.6719115434372336, tolerance: 0.014551840247178658
  tol, rng, random, positive)
/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 1.4863344737598774, tolerance: 0.014345245251133662
  tol, rng, random, positive)
/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 1.5224851375327852, tolerance: 0.014345245251133662
  tol, rng, random, positive)
/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: ConvergenceWarning: Objective did not converge. You might want t

/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 0.6236586011383682, tolerance: 0.014345245251133662
  tol, rng, random, positive)
/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 0.9332045141632763, tolerance: 0.014345245251133662
  tol, rng, random, positive)
/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 1.0813667647315905, tolerance: 0.014345245251133662
  tol, rng, random, positive)
/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: ConvergenceWarning: Objective did not converge. You might want t

/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 1.5076674356267579, tolerance: 0.014508286297718963
  tol, rng, random, positive)
/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 1.5577197896237225, tolerance: 0.014508286297718963
  tol, rng, random, positive)
/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 1.600528005582413, tolerance: 0.014508286297718963
  tol, rng, random, positive)
/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: ConvergenceWarning: Objective did not converge. You might want to

/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 0.8297514316574337, tolerance: 0.014508286297718963
  tol, rng, random, positive)
/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 1.2277423957872804, tolerance: 0.014508286297718963
  tol, rng, random, positive)
/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 1.4120912183071255, tolerance: 0.014508286297718963
  tol, rng, random, positive)
/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: ConvergenceWarning: Objective did not converge. You might want t

/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 1.4168155502900883, tolerance: 0.01428359825278988
  tol, rng, random, positive)
/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 1.4670178627596764, tolerance: 0.01428359825278988
  tol, rng, random, positive)
/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 1.510973814955165, tolerance: 0.01428359825278988
  tol, rng, random, positive)
/usr/local/lib/python3.7/site-packages/sklearn/linear_model/coordinate_descent.py:471: ConvergenceWarning: Objective did not converge. You might want to in

In [296]:
print(enetcv.score(tsx_train,tsy_train))
print(enetcv.score(tsx_test,tsy_test))
print(net_trainRMSE)
print(net_testRMSE)
print(net_testRMSE-net_trainRMSE)

0.9384564800381998
0.9295473554862679
0.09786614210377327
0.10913258806400852
0.011266445960235252


### Gradient Boosting

In [ ]:
gbm = GradientBoostingRegressor(max_depth=4, max_features='log2',
                                min_samples_leaf=15, min_samples_split=10, 
                                loss='huber')

In [174]:
para_gbm = {"n_estimators":np.arange(1000,10000,1000),'learning_rate':[0.05,0.1,0.5]}
gs_gbm = GridSearchCV(gbm, para_gbm, cv=10, scoring='neg_mean_squared_error', n_jobs=-1)
gs_gbm.fit(x_train, y_train)
gs_gbm.best_params_
#{'learning_rate': 0.05, 'n_estimators': 2000}

/usr/local/lib/python3.7/site-packages/sklearn/ensemble/gradient_boosting.py:1450: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


{'learning_rate': 0.05, 'n_estimators': 2000}

In [297]:
gbm.set_params(learning_rate = gs_gbm.best_params_['learning_rate'],\
                  n_estimators=gs_gbm.best_params_['n_estimators'])
gbm.fit(x_train, y_train)
score_gbm = gbm.score(x_train, y_train)
rmse_gbm = np.sqrt(mean_squared_error(y_train,gbm.predict(x_train)))
gbm_pred = np.expm1(gbm.predict(x_test))

/usr/local/lib/python3.7/site-packages/sklearn/ensemble/gradient_boosting.py:1450: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


In [300]:
gbm.set_params(learning_rate = gs_gbm.best_params_['learning_rate'],\
                  n_estimators=gs_gbm.best_params_['n_estimators'])
gbm.fit(tsx_train, tsy_train)
gbm_trainRMSE = np.sqrt(mean_squared_error(tsy_train, gbm.predict(tsx_train)))
gbm_testRMSE = np.sqrt(mean_squared_error(tsy_test, gbm.predict(tsx_test)))

/usr/local/lib/python3.7/site-packages/sklearn/ensemble/gradient_boosting.py:1450: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


In [301]:
print(gbm.score(tsx_train,tsy_train))
print(gbm.score(tsx_test,tsy_test))
print(gbm_trainRMSE)
print(gbm_testRMSE)
print(gbm_testRMSE-gbm_trainRMSE)

0.9777602934039485
0.9209912557928243
0.0588309456668239
0.11556953991501034
0.05673859424818645


In [303]:
sorted_importance = sorted(zip(x_train.columns, gbm.feature_importances_), key=lambda t:t[1], reverse=True)
sorted_importance

[('GrLivArea', 0.11998154182429836),
 ('OverallQual', 0.08070702009216647),
 ('TotalLivSF', 0.07600652753432594),
 ('TotalBsmtSF', 0.05769036814868799),
 ('YearBuilt', 0.049309456689671814),
 ('ExterQual', 0.04732207321431578),
 ('GarageCars', 0.04327307687077351),
 ('GarageArea', 0.03584284163609113),
 ('BsmtQual', 0.03229610244392319),
 ('FullBath', 0.031224992583582092),
 ('Fireplaces', 0.024262811848046704),
 ('LotFrontage', 0.023454846450426114),
 ('KitchenQual', 0.02269143915006779),
 ('YearRemodAdd', 0.02253784687679515),
 ('LotArea', 0.01954882438879911),
 ('TotRmsAbvGrd', 0.018739151812622812),
 ('1stFlrSF', 0.016772333687149983),
 ('GarageType_Attchd', 0.016664378126716707),
 ('CentralAir', 0.012776880272059398),
 ('FireplaceQu', 0.012555964557323038),
 ('HeatingQC', 0.012131790046045901),
 ('OverallCond', 0.01181074356952297),
 ('GarageYrBlt', 0.010986695103788385),
 ('MasVnrArea', 0.010919077087753814),
 ('BsmtFinSF1', 0.010720000389961315),
 ('MSZoning_RM', 0.0083067935431

### XGBoost

In [185]:
model_xgb = xgb.XGBRegressor(colsample_bytree=0.4603, min_child_weight=1.7817,
                             reg_alpha=0.4640,
                             reg_lambda=0.8571, subsample=0.5213, silent=1,
                             random_state =7, nthread = -1)

In [209]:
para_xgb = {"n_estimators":np.arange(1000,8000,1000),'learning_rate':[0.05,0.1,0.5],'gamma':[0.03,0.04,0.05]}
gs_xgb = GridSearchCV(model_xgb, para_xgb, cv=10, scoring='neg_mean_squared_error', n_jobs=-1)
gs_xgb.fit(x_train, y_train)
gs_xgb.best_params_
#{'gamma': 0.03, 'learning_rate': 0.05, 'n_estimators': 1000}

{'gamma': 0.03, 'learning_rate': 0.05, 'n_estimators': 1000}

In [239]:
model_xgb.set_params(learning_rate = gs_xgb.best_params_['learning_rate'],\
                       n_estimators=gs_xgb.best_params_['n_estimators'],\
                     gamma=gs_xgb.best_params_['gamma'])
model_xgb.fit(x_train, y_train)
score_xgb = model_xgb.score(x_train, y_train)
rmse_xgb = np.sqrt(mean_squared_error(y_train,model_xgb.predict(x_train)))
xgb_pred = np.expm1(model_xgb.predict(x_test))


0.07553247658018719

In [304]:
model_xgb.set_params(learning_rate = gs_xgb.best_params_['learning_rate'],\
                       n_estimators=gs_xgb.best_params_['n_estimators'],\
                     gamma=gs_xgb.best_params_['gamma'])
model_xgb.fit(tsx_train, tsy_train)
xgb_trainRMSE = np.sqrt(mean_squared_error(tsy_train, model_xgb.predict(tsx_train)))
xgb_testRMSE = np.sqrt(mean_squared_error(tsy_test, model_xgb.predict(tsx_test)))

In [305]:
print(model_xgb.score(tsx_train,tsy_train))
print(model_xgb.score(tsx_test,tsy_test))
print(xgb_trainRMSE)
print(xgb_testRMSE)
print(xgb_testRMSE-xgb_trainRMSE)

0.9639407793450944
0.9213488897914314
0.07491166860610257
0.1153076798181453
0.040396011212042726


In [307]:
sorted_importance_xgb = sorted(zip(x_train.columns, model_xgb.feature_importances_), key=lambda t:t[1], reverse=True)
sorted_importance_xgb

[('GarageCars', 0.1387865),
 ('OverallQual', 0.05728734),
 ('TotalLivSF', 0.051467437),
 ('CentralAir', 0.049059972),
 ('KitchenQual', 0.031065494),
 ('Fireplaces', 0.02857854),
 ('GarageCond', 0.02657734),
 ('MSZoning_RM', 0.02461435),
 ('MSZoning_C (all)', 0.024078827),
 ('GrLivArea', 0.023961123),
 ('BsmtQual', 0.021349309),
 ('YearRemodAdd', 0.019541861),
 ('Heating_Grav', 0.01949024),
 ('TotalBsmtSF', 0.017576464),
 ('BldgType_Twnhs', 0.017160263),
 ('ExterCond', 0.016279498),
 ('ExterQual', 0.014694732),
 ('GarageArea', 0.013602291),
 ('Heating_GasA', 0.012929943),
 ('Condition1_RRAe', 0.012871321),
 ('YearBuilt', 0.010486612),
 ('GarageType_Attchd', 0.010404091),
 ('OverallCond', 0.010117882),
 ('SaleType_New', 0.01006515),
 ('BldgType_1Fam', 0.009895855),
 ('GarageYrBlt', 0.009364027),
 ('1stFlrSF', 0.008192008),
 ('BldgType_Duplex', 0.00801875),
 ('LotArea', 0.008000854),
 ('Neighborhood_IDOTRR', 0.007668452),
 ('KitchenAbvGr', 0.0076543707),
 ('Condition1_Artery', 0.007535230

### Support vector regression

In [240]:
svr = SVR(epsilon = 0.1, gamma=1e-8,C=100000)
svr.fit(x_train,y_train) 
score_svr = svr.score(x_train, y_train)
rmse_svr = np.sqrt(mean_squared_error(y_train,svr.predict(x_train)))
svr_pred = np.expm1(svr.predict(x_test))

/usr/local/lib/python3.7/site-packages/sklearn/utils/validation.py:724: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


0.10759056392495969

In [308]:
svrts = SVR(epsilon = 0.1, gamma=1e-8,C=100000)
svrts.fit(tsx_train, tsy_train)
svr_trainRMSE = np.sqrt(mean_squared_error(tsy_train, svrts.predict(tsx_train)))
svr_testRMSE = np.sqrt(mean_squared_error(tsy_test, svrts.predict(tsx_test)))

/usr/local/lib/python3.7/site-packages/sklearn/utils/validation.py:724: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


In [309]:
print(svrts.score(tsx_train,tsy_train))
print(svrts.score(tsx_test,tsy_test))
print(svr_trainRMSE)
print(svr_testRMSE)
print(svr_testRMSE-svr_trainRMSE)

0.9231637274967383
0.9253323326581653
0.10935142498128915
0.1123497464920689
0.00299832151077975


### Stack model

In [241]:
ridge_b = make_pipeline(RobustScaler(), Ridge(alpha = 9.930467558623954, random_state=1))
lasso_b = make_pipeline(RobustScaler(), Lasso(alpha = 0.0003503034741265338, random_state=1))
ElNet_b = ElasticNet(alpha = 0.0003880510732210184, l1_ratio = 0.9)
svr_b = SVR(epsilon = 0.1, gamma=1e-8,C=100000)
model_xgb_b = xgb.XGBRegressor(gamma = 0.03, learning_rate = 0.05, n_estimators = 1000,
                             colsample_bytree=0.4603, min_child_weight=1.7817,
                             reg_alpha=0.4640,
                             reg_lambda=0.8571, subsample=0.5213, silent=1,
                             random_state =7, nthread = -1)
gbm_b = GradientBoostingRegressor(learning_rate = 0.05, n_estimators = 2000,
                                  max_depth=4, max_features='log2',
                                  min_samples_leaf=15, min_samples_split=10, 
                                  loss='huber')

In [315]:
stackmodel = StackingRegressor(
        regressors=[ElNet_b, lasso_b, ridge_b, svr_b, model_xgb_b, gbm_b],
        meta_regressor=SVR(kernel='rbf')
    )
stkts = StackingRegressor(
        regressors=[ElNet_b, lasso_b, ridge_b, svr_b, model_xgb_b, gbm_b],
        meta_regressor=SVR(kernel='rbf')
    )

In [316]:
stackmodel.fit(x_train, y_train)

stacked = stackmodel.predict(x_test)
rmse_stacked = np.sqrt(mean_squared_error(y_train,stackmodel.predict(x_train)))
stacked_pred = np.expm1(stacked)
stkts.fit(tsx_train, tsy_train)
stk_trainRMSE = np.sqrt(mean_squared_error(tsy_train, stkts.predict(tsx_train)))
stk_testRMSE = np.sqrt(mean_squared_error(tsy_test, stkts.predict(tsx_test)))

/usr/local/lib/python3.7/site-packages/sklearn/utils/validation.py:724: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/usr/local/lib/python3.7/site-packages/sklearn/ensemble/gradient_boosting.py:1450: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/usr/local/lib/python3.7/site-packages/sklearn/utils/validation.py:724: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
/usr/local/lib/python3.7/site-packages/sklearn/svm/base.py:193: FutureWarning: The default value of gamma will change from 'auto' to 'scale' in version 0.22 to account better for unscaled features. Set gamm

In [317]:
print(stkts.score(tsx_train,tsy_train))
print(stkts.score(tsx_test,tsy_test))
print(stk_trainRMSE)
print(stk_testRMSE)
print(stk_testRMSE-stk_trainRMSE)

0.9780964814775633
0.92045838879446
0.05838459136321828
0.11595860892017781
0.05757401755695953


In [244]:
# Best one
ensembled = np.expm1((0.25 * ridge.predict(x_test).reshape(-1,1)) +
                     (0.2 * ElNet.predict(x_test).reshape(-1,1)) +
                     (0.2 * lasso.predict(x_test).reshape(-1,1)) +
                     (0.15 * model_xgb.predict(x_test).reshape(-1,1)) +
                     (0.2 * GBoost.predict(x_test).reshape(-1,1)))

In [329]:
obj = pd.DataFrame([[score_ridge,rmse_ridge,rdg_trainRMSE,rdg_testRMSE,rmse_ridge_test-rmse_ridge_train],
                    [score_lasso,rmse_lasso,lso_trainRMSE,lso_testRMSE,lso_testRMSE-lso_trainRMSE],
                    [score_ElNet,rmse_ElNet,net_trainRMSE,net_testRMSE,net_testRMSE-net_trainRMSE],
                    [score_gbm,rmse_gbm,gbm_trainRMSE,gbm_testRMSE,gbm_testRMSE-gbm_trainRMSE],
                    [score_xgb,rmse_xgb,xgb_trainRMSE,xgb_testRMSE,xgb_testRMSE-xgb_trainRMSE],
                    [score_svr,rmse_svr,svr_trainRMSE,svr_testRMSE,svr_testRMSE-svr_trainRMSE]],
                   columns = ['score_grid','RMSE','train_RMSE','test_RMSE','diff_RMSE'],
                   index=['Ridge','Lasso','ElNet','GBM','XGB','SVR'])
obj

score_grid      RMSE  train_RMSE  test_RMSE  diff_RMSE
Ridge    0.940449  0.097509    0.097555   0.109320  -0.000415
Lasso    0.939068  0.098633    0.098876   0.107920   0.009044
ElNet    0.939095  0.098611    0.097866   0.109133   0.011266
GBM      0.976761  0.060912    0.058831   0.115570   0.056739
XGB      0.964267  0.075532    0.074912   0.115308   0.040396
SVR      0.927498  0.107591    0.109351   0.112350   0.002998

In [340]:
sub = pd.DataFrame()
sub['Id'] = df_test.Id
sub['SalePrice'] = ensembled
sub.to_csv('submission.csv',index=False)